# "Eleições RJ: Votação dos Deputados por Bairros (capital)"
> "dados do TSE"

- toc: true
- branch: master
- badges: true
- comments: false
- numbersections: true
- categories: [eleições, RJ, bairros]
- image: images/some_folder/your_image.png
- hide: false
- search_exclude: true

In [1]:
#hide

import os
from IPython.core.display import display, HTML
import pandas as pd

import electionsBR as el
import LabFunctions as lab
from EppDataBase import EppDataBase

epp = EppDataBase()

def get_dict_candidatxs(uf,ano,cargo,partidos,only_elected=True):
    elected = get_elected_candidates_dict(uf,partidos,cargos=[cargo],anos=[ano],only_elected=only_elected)
    df = elected[cargo][ano].copy()
    # else:
    #     pass
    # df['num_nome'] = df['NUMERO_CANDIDATO'].astype(str) + ' - ' + df['NOME_CANDIDATO']
    df['num_nome'] = df['NUMERO_CANDIDATO'] + ' - ' + df['NOME_CANDIDATO']
    return df.set_index('NUMERO_CANDIDATO')['num_nome'].to_dict()

def show_folium(m):
    data = m.get_root().render()
    data_fixed_height = data.replace('width: 100%;height: 100%', 'width: 100%').replace('height: 100.0%;', 'height: 609px;', 1)
    # display(HTML(data_fixed_height))
    return data_fixed_height

def plot_candidates_bars(epp,ano,uf,n_turno,cargo,municipio,partidos,only_elected,group_level,selected_col,relative, nr_partidos,nrows=None):
    selection_dict = {'NR_TURNO':n_turno,'DS_CARGO':cargo,'NM_MUNICIPIO':municipio}
    # dict_candidatxs = get_dict_candidatxs(elected,ano,cargo)
    # partidos=partidos_esquerda

    if cargo == 'VEREADOR':
        # dict_candidatxs = {}
        
        df = epp.get_results_df(ano,uf)
        df_dict = df.loc[df['nr_partido'].isin(nr_partidos)].copy()
        df_dict['NR_VOTAVEL'] = df_dict['NR_VOTAVEL'].astype(str)
        df_dict['nome'] = df_dict['NR_VOTAVEL'] + ' - ' + df_dict['NM_VOTAVEL']
        dict_candidatxs = df_dict.set_index('NR_VOTAVEL')['nome'].to_dict()
        only_elected = False
    else:
        dict_candidatxs = get_dict_candidatxs(uf,ano,cargo,partidos=partidos_esquerda,only_elected=only_elected)
        dict_candidatxs['13'] = '13 - PT'
        dict_candidatxs['50'] = '50 - PSOL'
        dict_candidatxs['65'] = '65 - PCdoB'

    df_bairros = lab.get_group_results(ano,uf,selection_dict,group_level,selected_col=selected_col,relative=relative,dict_candidatxs=dict_candidatxs)

    # selected_cols = [col for col in df_bairros.columns if col[:2] in numeros_partidos]
    # df_bairros = df_bairros[selected_cols]


    sufix = 'eleitos_' if only_elected else 'todos_'
    sufix += 'relativo' if relative else 'absoluto'
    folder_path = 'results/votacao_NM_BAIRRO'
    os.makedirs(folder_path,exist_ok=True)
    fname = f'{ano}_RJ_{cargo}_{"_".join(partidos)}_{sufix}.csv'.replace(' ','_')
    df_bairros = df_bairros.reset_index(drop=True)
    if not relative:
        df_bairros.iloc[:,2:] = df_bairros.iloc[:,2:].astype(int)
        # df_bairros.iloc[:,2:] = df_bairros.select_dtypes(include='number').astype(int)
    df_bairros = df_bairros.copy()
    df_bairros['SOMA'] = df_bairros.sum(axis=1,numeric_only=True)
    df_bairros = df_bairros.sort_values(by='SOMA',ascending=False)
    df_bairros.to_csv(f'{folder_path}/{fname}',index=False,sep=';')
    if nrows:
        df_bairros = df_bairros.head(nrows)
    df_bairros.index = range(1,len(df_bairros)+1)
    df_style = df_bairros.style.bar(color='#d65f5f')
    return df_style


def get_elected_candidates_dict(uf,partidos,cargos,anos,only_elected=True,verbose=False):
    if only_elected:
        folder_path = 'results/eleitos'
    else:
        folder_path = 'results/candidatos'
    os.makedirs(folder_path,exist_ok=True)
    elected = {}
    for cargo in cargos:
        cargo_api = ' '.join([x.capitalize() for x in cargo.split()])
        elected[cargo] = {}
        for ano in anos:
            fname = f'{ano}_{uf}_{cargo}_{"_".join(partidos)}.csv'.replace(' ','_')
            file_path = f'{folder_path}/{fname}'
            if verbose:
                print(file_path)
            if not os.path.exists(file_path):
                if only_elected:
                    cand = el.get_candidates(year=ano, position=cargo_api,only_elected=only_elected,
                        columns=["NUMERO_CANDIDATO", "NOME_CANDIDATO", "SIGLA_UF", "NUM_TURNO", "SIGLA_PARTIDO", "COMPOSICAO_LEGENDA"])
                else:
                    cand = el.get_candidates(year=ano, position=cargo_api,
                        columns=["NUMERO_CANDIDATO", "NOME_CANDIDATO", "SIGLA_UF", "NUM_TURNO", "SIGLA_PARTIDO", "COMPOSICAO_LEGENDA"])

                cand = cand.query(f"SIGLA_UF == '{uf}' ").query(f"SIGLA_PARTIDO in {partidos}")
                cand.to_csv(file_path,index=False)
            else:
                cand = pd.read_csv(file_path)
                # cand['']
                cand['NUMERO_CANDIDATO'] = cand['NUMERO_CANDIDATO'].astype(str)
            
            elected[cargo][ano] = cand
            
    return elected


n_turno = 1
uf = 'RJ'
anos = [2014,2018]

partidos_esquerda = ['PT','PSOL','PC do B']
cand_elections_fed = {}

cargos= ["DEPUTADO FEDERAL","DEPUTADO ESTADUAL"]

## Deputado Federal - 2018

In [2]:
#hide

ano = 2018
cargo = 'DEPUTADO FEDERAL' 
# cargo = 'DEPUTADO ESTADUAL'

dict_candidatxs = get_dict_candidatxs(uf,ano,cargo,partidos=partidos_esquerda)
lista_cand = list(dict_candidatxs.keys())

print(f'{uf} - {ano} - {cargo}:\n')
for cand in lista_cand:
    print(dict_candidatxs[cand])

RJ - 2018 - DEPUTADO FEDERAL:

1377 - BENEDITA SOUZA DA SILVA SAMPAIO 
5005 - JEAN WYLLYS DE MATOS SANTOS
5050 - MARCELO RIBEIRO FREIXO
5077 - TALIRIA PETRONE SOARES
5080 - GLAUBER DE MEDEIROS BRAGA
6565 - JANDIRA FEGHALI


**Tabela de votação por bairro - absoluto**

In [3]:
#hide_input
#collapse_output

municipio= 'RIO DE JANEIRO'
print(f'município selecionado: {municipio}')
group_level = 'NM_BAIRRO' #  NM_BAIRRO NM_LOCAL_VOTACAO
selected_col='NR_VOTAVEL'
nr_partidos=[13,50,65]
relative = False
only_elected=True
nrows=None

plot_candidates_bars(epp,ano,uf,n_turno,cargo,municipio,partidos_esquerda,only_elected,group_level,selected_col,relative, nr_partidos,nrows)

município selecionado: RIO DE JANEIRO


**Tabela de votação por bairro - relativo**

In [4]:
#hide_input
#collapse_output
 
relative = True
plot_candidates_bars(epp,ano,uf,n_turno,cargo,municipio,partidos_esquerda,only_elected,group_level,selected_col,relative, nr_partidos,nrows)

## Deputado Estadual - 2018
**Tabela de votação por bairro - absoluto**

In [5]:
#hide_input
#collapse_output

ano - 2018
cargo = 'DEPUTADO ESTADUAL'

municipio= 'RIO DE JANEIRO'
print(f'município selecionado: {municipio}')
group_level = 'NM_BAIRRO' #  NM_BAIRRO NM_LOCAL_VOTACAO
selected_col='NR_VOTAVEL'
nr_partidos=[13,50,65]
relative = False
only_elected=True

plot_candidates_bars(epp,ano,uf,n_turno,cargo,municipio,partidos_esquerda,only_elected,group_level,selected_col,relative, nr_partidos,nrows)

município selecionado: RIO DE JANEIRO


**Tabela de votação por bairro - relativo**

In [6]:
#hide_input
#collapse_output
 
relative = True
plot_candidates_bars(epp,ano,uf,n_turno,cargo,municipio,partidos_esquerda,only_elected,group_level,selected_col,relative, nr_partidos, nrows)

## Vereador - 2020

In [7]:
#hide_input
#collapse_output

ano = 2020
cargo = 'VEREADOR'

municipio= 'RIO DE JANEIRO'
print(f'município selecionado: {municipio}')
group_level = 'NM_BAIRRO' #  NM_BAIRRO NM_LOCAL_VOTACAO
selected_col='NR_VOTAVEL'
nr_partidos=[13,50,65]
relative = False
only_elected=True

plot_candidates_bars(epp,ano,uf,n_turno,cargo,municipio,partidos_esquerda,only_elected,group_level,selected_col,relative, nr_partidos,nrows)

município selecionado: RIO DE JANEIRO
Adicionando resultado...
Lendo dados do arquivo 'data/votacao_secao_2020_RJ/votacao_secao_2020_RJ.csv'.


**Tabela de votação por bairro - relativo**

In [8]:
#hide_input
#collapse_output

relative = True
plot_candidates_bars(epp,ano,uf,n_turno,cargo,municipio,partidos_esquerda,only_elected,group_level,selected_col,relative, nr_partidos, nrows)

In [9]:
#hide

group_level = 'NM_BAIRRO' #  NM_BAIRRO NM_LOCAL_VOTACAO
selected_col='NR_VOTAVEL'
relative = True
use_max_scale = False

selection_dict = {'NR_TURNO':n_turno,'NM_MUNICIPIO':'RIO DE JANEIRO','DS_CARGO':cargo}

df_bairros = lab.get_group_results(ano,uf,selection_dict,group_level,selected_col=selected_col,relative=relative,dict_candidatxs=dict_candidatxs)
bairros_geo = 'geojson/limites_bairros_RJ_edit.geojson'
cargo = cargo.replace(' ','_')
rel_type = 'relativo' if relative else 'absoluto'

folder_path=f'maps/{ano}_{uf}_{cargo}/{rel_type}'
if relative:
    max_scale = df_bairros.max().iloc[2:].max() if use_max_scale else 0
    folder_path += '_{:.3f}'.format(max_scale)
else:
    max_scale = None

# os.makedirs(folder_path,exist_ok=True)

# for numero,nome in dict_candidatxs.items():
#     print(f'gerando imagem de {nome}')
#     m = lab.get_map(bairros_geo,df_bairros,numero,nome,max_scale)
    
#     lab.map2png(m,folder_path=folder_path,filename = f'/{nome}.png')

ValueError: '1377' is not in list

In [ ]:
#hide
# 
# #hide_input
# #collapse_output

municipio= 'RIO DE JANEIRO'
i = 2
num = lista_cand[i]

group_level = 'NM_BAIRRO' #  NM_BAIRRO NM_LOCAL_VOTACAO
selected_col='NR_VOTAVEL'
relative = True
relative = False
use_max_scale = False
selection_dict = {'NR_TURNO':n_turno,'NM_MUNICIPIO':municipio,'DS_CARGO':cargo}
df_bairros = lab.get_group_results(ano,uf,selection_dict,group_level,selected_col=selected_col,relative=relative,dict_candidatxs=dict_candidatxs)
bairros_geo = 'geojson/limites_bairros_RJ_edit.geojson'
m = lab.get_map(bairros_geo,df_bairros,num,dict_candidatxs[num],0.0)
m
# data_fixed_height = show_folium(m)

# display(HTML(data_fixed_height))
# df_bairros

# data = m.get_root().render()
# data.replace('width: 100%;height: 100%', 'width: 100%')
# data_fixed_height = data.replace('width: 100%;height: 100%', 'width: 100%').replace('height: 100.0%;', 'height: 609px;', 1)
    

In [ ]:
#hide

# #hide_input
# #collapse_output

relative = True
df_bairros = lab.get_group_results(ano,uf,selection_dict,group_level,selected_col=selected_col,relative=relative,dict_candidatxs=dict_candidatxs)
m = lab.get_map(bairros_geo,df_bairros,num,dict_candidatxs[num],0.0)
# data_fixed_height = show_folium(m)
m

# display(HTML(data_fixed_height))